In [1]:
!pip install textblob
!pip install pyspellchecker
!pip install spacy
!python -m spacy download pt_core_news_sm
import pandas as pd
pd.set_option('display.max_rows', None)
import nltk
nltk.download('punkt')
from nltk.tokenize import word_tokenize
nltk.download('stopwords')
from nltk.corpus import stopwords
import sklearn
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.naive_bayes import MultinomialNB
from sklearn import svm
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report
from sklearn.metrics import precision_recall_fscore_support
from sklearn.model_selection import GridSearchCV
import joblib
from spellchecker import SpellChecker
from nltk.stem import WordNetLemmatizer
import spacy

     -------------------------------------- 636.8/636.8 kB 1.3 MB/s eta 0:00:00
     ---------------------------------------- 3.4/3.4 MB 1.5 MB/s eta 0:00:00
     ---------------------------------------- 12.2/12.2 MB 2.4 MB/s eta 0:00:00
     ---------------------------------------- 2.1/2.1 MB 3.2 MB/s eta 0:00:00
     -------------------------------------- 181.6/181.6 kB 2.7 MB/s eta 0:00:00
     ---------------------------------------- 1.5/1.5 MB 4.7 MB/s eta 0:00:00
     -------------------------------------- 480.9/480.9 kB 4.3 MB/s eta 0:00:00
     ---------------------------------------- 94.7/94.7 kB 1.8 MB/s eta 0:00:00
     -------------------------------------- 48.9/48.9 kB 821.7 kB/s eta 0:00:00
     ---------------------------------------- 7.0/7.0 MB 3.7 MB/s eta 0:00:00
     ---------------------------------------- 13.0/13.0 MB 2.1 MB/s eta 0:00:00
[+] Download and installation successful
You can now load the package via spacy.load('pt_core_news_sm')


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\pedro\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping tokenizers\punkt.zip.
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\pedro\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping corpora\stopwords.zip.


In [2]:
stop_words = stopwords.words('portuguese')

In [3]:
dados_treino = pd.read_csv('dados_para_treinamento.csv')

In [4]:
dados_treino

Comentarios  \
0     Vejam só, o celular lg b22 que comprei em jane...   
1     A bateria dura pouco, e pra um telefone desse ...   
2     Comprei pra minha achando que era o original i...   
3     O produto não é de boa qualidade e não é cadas...   
4     O aparelho não sei o porquê a bateria acaba mu...   
5     Para minha mãe que e idosa, atende bem as expe...   
6     Se da doido nao vale nada e nao consegui nem d...   
7     O celular não tem a opção pra tira o número co...   
8     Não recomendo este lg b220.\nComprei-o para su...   
9            Celular não para carregado. Volume é ruim.   
10    Bom mas ele deu ploblema ele nao ficiona mais ...   
11    Ola pensei q era melhor so dois mes de uso ja ...   
12    O visor é muito pequeno e as letras miúdas! se...   
13    Muito ruim de sinal nem na cidade pega direito...   
14                     Péssima qualidade não recomendo.   
15    Boa tarde!.\nEu estou entrando em contato com ...   
16    Produto muito fraco nao chega nem aos pes dos ...   
17    Muito ruim! o celular não durou nem dois meses...   
18    Funciona perfeitamente porem p celular e uma r...   
19    Não tive sorte o carregador não entrar o áudio...   
20    Produto pirata! made in china. Sério, tá escri...   
21    O celular é horrivel de sinal,mesmo ligado a a...   
22    Ótimo,diferente dos celulares modernos que faz...   
23    Comprei pro meu pai, celular de cara ja não de...   
24    Era o que eu espera. Um celular simples,seguro...   
25                           Da forma que eu esperava!.   
26    Aparelho horrível não durou 7 meses a tela fic...   
27                               Atende bem o esperado.   
28    Produto péssimo pensei que era original me arr...   
29                                       Boa qualidade.   
30                              Ruim, não recomendo!!!.   
31                                               Ótimo.   
32    Excelente produto para o que o precisa, muito ...   
33                                             Péssimo.   
34                                   Produto muito bom.   
35           Produto veio com defeito já foi devolvido.   
36                                               Otimo.   
37    Depois de 5 meses a bateria não recarrega mais...   
38                                   Ótimo telefone, 👍.   
39                          Bom pra quem só quer ligar.   
40    Não pegou sinal muito ruim, e comprei na cor a...   
41                                                   👍.   
42    Produto co. Defeito no dia que mais orecisei t...   
43                                              Atende.   
44                                   Muito bom produto.   
45                 O aparelho é ótimo minha mãe adorou.   
46                                        Gostei muito.   
47                                           Muito bom.   
48                                            Mt bom 👍.   
49               Atende minhas necessidades, recomendo.   
50                                Não reconhece o chip.   
51    Amei o celular. Bateria dura muito tempo. Top ...   
52                                       Otimo produto.   
53    Ainda não usei, porém parece que é de boa qual...   
54                                          Bom gostei.   
55                                          Muito bom!.   
56                                 Muito bom recomendo.   
57                         Ótimo preço e ótimo produto.   
58    Mandaram celular com bateria inchada brincadei...   
59    Caro não vale tudo isto rui de bateria e de to...   
60          Bateria não dura 2 horas, pessimo negocio,.   
61                              Telefone veio quebrado.   
62             Muito bom para fazer e receber ligações.   
63                                    Gostei muito bom.   
64                                O celular veio preto.   
65                                         Vale a pena.   
66                  Gostei demais. Simples e funcional.   
67       Eu achei o meu produto 

In [5]:
def corretora(dataset):
    dataset_corrigido = dataset.copy()
    spell = SpellChecker(language='pt')
    for i, comentario in enumerate(dataset_corrigido["Comentarios"]):
        palavras = comentario.split()
        palavras_corrigidas = [spell.correction(palavra) for palavra in palavras]
        palavras_corrigidas = [p if p is not None else '' for p in palavras_corrigidas]
        comentario_corrigido = ' '.join(palavras_corrigidas)
        dataset_corrigido.at[i, "Comentarios"] = comentario_corrigido
    return dataset_corrigido

In [6]:
def tokeniza(dataset):
    dataset.dropna(subset=['Comentarios'], inplace=True)
    dataset['tokens'] = dataset['Comentarios'].apply(lambda x: word_tokenize(x.lower()))
    return dataset

In [7]:
def limpa(dataset):
    for i, tokens in enumerate(dataset['tokens']):
        dataset['tokens'][i] = [token for token in tokens if token.isalpha()]
    return dataset

In [9]:
def removeStopWords(dataset):
    stop_words_pt = set(stopwords.words('portuguese'))
    stop_words_pt.remove('não')
    for i, tokens in enumerate(dataset['tokens']):
        dataset['tokens'][i] = [token for token in tokens if token not in stop_words_pt]
    return dataset

In [10]:
def vetoriza(dataset):
    tfidf = TfidfVectorizer()
    tokens_vetorizados = tfidf.fit_transform(dataset['tokens'].apply(lambda x: ' '.join(x)))
    print("Parâmetros de Vetorização:")
    print(tfidf.get_params())
    return tokens_vetorizados

In [11]:
def codificaRotulos(dataset):
    encoder = LabelEncoder()
    target_codificado = encoder.fit_transform(dataset['Rotulo'])
    return target_codificado

In [12]:
def modeladoraNB(matrizVetores, rotulos_codificados):
    X_train, X_test, y_train, y_test = train_test_split(matrizVetores, rotulos_codificados, test_size=0.25, random_state=42)
    modelo = MultinomialNB(alpha=0.1)#, class_prior=None, fit_prior=True)
    modelo.fit(X_train, y_train)
    y_pred = modelo.predict(X_test)
    precision, recall, f1, _ = precision_recall_fscore_support(y_test, y_pred, average='weighted', zero_division=1)
    print(classification_report(y_test, y_pred))
    score = modelo.score(X_test, y_test)
    print("Acurácia do modelo: {:.2f}%".format(score*100))
    return modelo

In [13]:
def modeladoraSVM(matrizVetores, rotulos_codificados):
    X_train, X_test, y_train, y_test = train_test_split(matrizVetores, rotulos_codificados, test_size=0.15, random_state=42)
    modelo = svm.SVC(kernel='rbf', C=1, gamma='scale', degree=1)
    modelo.fit(X_train, y_train)
    y_pred = modelo.predict(X_test)
    print(classification_report(y_test, y_pred))
    score = modelo.score(X_test, y_test)
    print("Acurácia do modelo: {:.2f}%".format(score*100))
    return modelo

In [15]:
def modeladoraRandomForest(matrizVetores, rotulos_codificados):
    X_train, X_test, y_train, y_test = train_test_split(matrizVetores, rotulos_codificados, test_size=0.25, random_state=42)
    modelo = RandomForestClassifier()
    modelo.fit(X_train, y_train)
    y_pred = modelo.predict(X_test)
    print(classification_report(y_test, y_pred))
    score = modelo.score(X_test, y_test)
    print("Acurácia do modelo: {:.2f}%".format(score*100))
    return modelo

In [16]:
dados_tokenizados = tokeniza(dados_treino)

In [17]:
dados_tokenizados

Comentarios  \
0     Vejam só, o celular lg b22 que comprei em jane...   
1     A bateria dura pouco, e pra um telefone desse ...   
2     Comprei pra minha achando que era o original i...   
3     O produto não é de boa qualidade e não é cadas...   
4     O aparelho não sei o porquê a bateria acaba mu...   
5     Para minha mãe que e idosa, atende bem as expe...   
6     Se da doido nao vale nada e nao consegui nem d...   
7     O celular não tem a opção pra tira o número co...   
8     Não recomendo este lg b220.\nComprei-o para su...   
9            Celular não para carregado. Volume é ruim.   
10    Bom mas ele deu ploblema ele nao ficiona mais ...   
11    Ola pensei q era melhor so dois mes de uso ja ...   
12    O visor é muito pequeno e as letras miúdas! se...   
13    Muito ruim de sinal nem na cidade pega direito...   
14                     Péssima qualidade não recomendo.   
15    Boa tarde!.\nEu estou entrando em contato com ...   
16    Produto muito fraco nao chega nem aos pes dos ...   
17    Muito ruim! o celular não durou nem dois meses...   
18    Funciona perfeitamente porem p celular e uma r...   
19    Não tive sorte o carregador não entrar o áudio...   
20    Produto pirata! made in china. Sério, tá escri...   
21    O celular é horrivel de sinal,mesmo ligado a a...   
22    Ótimo,diferente dos celulares modernos que faz...   
23    Comprei pro meu pai, celular de cara ja não de...   
24    Era o que eu espera. Um celular simples,seguro...   
25                           Da forma que eu esperava!.   
26    Aparelho horrível não durou 7 meses a tela fic...   
27                               Atende bem o esperado.   
28    Produto péssimo pensei que era original me arr...   
29                                       Boa qualidade.   
30                              Ruim, não recomendo!!!.   
31                                               Ótimo.   
32    Excelente produto para o que o precisa, muito ...   
33                                             Péssimo.   
34                                   Produto muito bom.   
35           Produto veio com defeito já foi devolvido.   
36                                               Otimo.   
37    Depois de 5 meses a bateria não recarrega mais...   
38                                   Ótimo telefone, 👍.   
39                          Bom pra quem só quer ligar.   
40    Não pegou sinal muito ruim, e comprei na cor a...   
41                                                   👍.   
42    Produto co. Defeito no dia que mais orecisei t...   
43                                              Atende.   
44                                   Muito bom produto.   
45                 O aparelho é ótimo minha mãe adorou.   
46                                        Gostei muito.   
47                                           Muito bom.   
48                                            Mt bom 👍.   
49               Atende minhas necessidades, recomendo.   
50                                Não reconhece o chip.   
51    Amei o celular. Bateria dura muito tempo. Top ...   
52                                       Otimo produto.   
53    Ainda não usei, porém parece que é de boa qual...   
54                                          Bom gostei.   
55                                          Muito bom!.   
56                                 Muito bom recomendo.   
57                         Ótimo preço e ótimo produto.   
58    Mandaram celular com bateria inchada brincadei...   
59    Caro não vale tudo isto rui de bateria e de to...   
60          Bateria não dura 2 horas, pessimo negocio,.   
61                              Telefone veio quebrado.   
62             Muito bom para fazer e receber ligações.   
63                                    Gostei muito bom.   
64                                O celular veio preto.   
65                                         Vale a pena.   
66                  Gostei demais. Simples e funcional.   
67       Eu achei o meu produto 

In [18]:
palavras = limpa(dados_tokenizados)

In [19]:
palavras

Comentarios  \
0     Vejam só, o celular lg b22 que comprei em jane...   
1     A bateria dura pouco, e pra um telefone desse ...   
2     Comprei pra minha achando que era o original i...   
3     O produto não é de boa qualidade e não é cadas...   
4     O aparelho não sei o porquê a bateria acaba mu...   
5     Para minha mãe que e idosa, atende bem as expe...   
6     Se da doido nao vale nada e nao consegui nem d...   
7     O celular não tem a opção pra tira o número co...   
8     Não recomendo este lg b220.\nComprei-o para su...   
9            Celular não para carregado. Volume é ruim.   
10    Bom mas ele deu ploblema ele nao ficiona mais ...   
11    Ola pensei q era melhor so dois mes de uso ja ...   
12    O visor é muito pequeno e as letras miúdas! se...   
13    Muito ruim de sinal nem na cidade pega direito...   
14                     Péssima qualidade não recomendo.   
15    Boa tarde!.\nEu estou entrando em contato com ...   
16    Produto muito fraco nao chega nem aos pes dos ...   
17    Muito ruim! o celular não durou nem dois meses...   
18    Funciona perfeitamente porem p celular e uma r...   
19    Não tive sorte o carregador não entrar o áudio...   
20    Produto pirata! made in china. Sério, tá escri...   
21    O celular é horrivel de sinal,mesmo ligado a a...   
22    Ótimo,diferente dos celulares modernos que faz...   
23    Comprei pro meu pai, celular de cara ja não de...   
24    Era o que eu espera. Um celular simples,seguro...   
25                           Da forma que eu esperava!.   
26    Aparelho horrível não durou 7 meses a tela fic...   
27                               Atende bem o esperado.   
28    Produto péssimo pensei que era original me arr...   
29                                       Boa qualidade.   
30                              Ruim, não recomendo!!!.   
31                                               Ótimo.   
32    Excelente produto para o que o precisa, muito ...   
33                                             Péssimo.   
34                                   Produto muito bom.   
35           Produto veio com defeito já foi devolvido.   
36                                               Otimo.   
37    Depois de 5 meses a bateria não recarrega mais...   
38                                   Ótimo telefone, 👍.   
39                          Bom pra quem só quer ligar.   
40    Não pegou sinal muito ruim, e comprei na cor a...   
41                                                   👍.   
42    Produto co. Defeito no dia que mais orecisei t...   
43                                              Atende.   
44                                   Muito bom produto.   
45                 O aparelho é ótimo minha mãe adorou.   
46                                        Gostei muito.   
47                                           Muito bom.   
48                                            Mt bom 👍.   
49               Atende minhas necessidades, recomendo.   
50                                Não reconhece o chip.   
51    Amei o celular. Bateria dura muito tempo. Top ...   
52                                       Otimo produto.   
53    Ainda não usei, porém parece que é de boa qual...   
54                                          Bom gostei.   
55                                          Muito bom!.   
56                                 Muito bom recomendo.   
57                         Ótimo preço e ótimo produto.   
58    Mandaram celular com bateria inchada brincadei...   
59    Caro não vale tudo isto rui de bateria e de to...   
60          Bateria não dura 2 horas, pessimo negocio,.   
61                              Telefone veio quebrado.   
62             Muito bom para fazer e receber ligações.   
63                                    Gostei muito bom.   
64                                O celular veio preto.   
65                                         Vale a pena.   
66                  Gostei demais. Simples e funcional.   
67       Eu achei o meu produto 

In [20]:
palavras_mais_importantes = removeStopWords(palavras)

In [21]:
palavras_mais_importantes

Comentarios  \
0     Vejam só, o celular lg b22 que comprei em jane...   
1     A bateria dura pouco, e pra um telefone desse ...   
2     Comprei pra minha achando que era o original i...   
3     O produto não é de boa qualidade e não é cadas...   
4     O aparelho não sei o porquê a bateria acaba mu...   
5     Para minha mãe que e idosa, atende bem as expe...   
6     Se da doido nao vale nada e nao consegui nem d...   
7     O celular não tem a opção pra tira o número co...   
8     Não recomendo este lg b220.\nComprei-o para su...   
9            Celular não para carregado. Volume é ruim.   
10    Bom mas ele deu ploblema ele nao ficiona mais ...   
11    Ola pensei q era melhor so dois mes de uso ja ...   
12    O visor é muito pequeno e as letras miúdas! se...   
13    Muito ruim de sinal nem na cidade pega direito...   
14                     Péssima qualidade não recomendo.   
15    Boa tarde!.\nEu estou entrando em contato com ...   
16    Produto muito fraco nao chega nem aos pes dos ...   
17    Muito ruim! o celular não durou nem dois meses...   
18    Funciona perfeitamente porem p celular e uma r...   
19    Não tive sorte o carregador não entrar o áudio...   
20    Produto pirata! made in china. Sério, tá escri...   
21    O celular é horrivel de sinal,mesmo ligado a a...   
22    Ótimo,diferente dos celulares modernos que faz...   
23    Comprei pro meu pai, celular de cara ja não de...   
24    Era o que eu espera. Um celular simples,seguro...   
25                           Da forma que eu esperava!.   
26    Aparelho horrível não durou 7 meses a tela fic...   
27                               Atende bem o esperado.   
28    Produto péssimo pensei que era original me arr...   
29                                       Boa qualidade.   
30                              Ruim, não recomendo!!!.   
31                                               Ótimo.   
32    Excelente produto para o que o precisa, muito ...   
33                                             Péssimo.   
34                                   Produto muito bom.   
35           Produto veio com defeito já foi devolvido.   
36                                               Otimo.   
37    Depois de 5 meses a bateria não recarrega mais...   
38                                   Ótimo telefone, 👍.   
39                          Bom pra quem só quer ligar.   
40    Não pegou sinal muito ruim, e comprei na cor a...   
41                                                   👍.   
42    Produto co. Defeito no dia que mais orecisei t...   
43                                              Atende.   
44                                   Muito bom produto.   
45                 O aparelho é ótimo minha mãe adorou.   
46                                        Gostei muito.   
47                                           Muito bom.   
48                                            Mt bom 👍.   
49               Atende minhas necessidades, recomendo.   
50                                Não reconhece o chip.   
51    Amei o celular. Bateria dura muito tempo. Top ...   
52                                       Otimo produto.   
53    Ainda não usei, porém parece que é de boa qual...   
54                                          Bom gostei.   
55                                          Muito bom!.   
56                                 Muito bom recomendo.   
57                         Ótimo preço e ótimo produto.   
58    Mandaram celular com bateria inchada brincadei...   
59    Caro não vale tudo isto rui de bateria e de to...   
60          Bateria não dura 2 horas, pessimo negocio,.   
61                              Telefone veio quebrado.   
62             Muito bom para fazer e receber ligações.   
63                                    Gostei muito bom.   
64                                O celular veio preto.   
65                                         Vale a pena.   
66                  Gostei demais. Simples e funcional.   
67       Eu achei o meu produto 

In [22]:
matrizVetores = vetoriza(palavras_mais_importantes)

Parâmetros de Vetorização:
{'analyzer': 'word', 'binary': False, 'decode_error': 'strict', 'dtype': <class 'numpy.float64'>, 'encoding': 'utf-8', 'input': 'content', 'lowercase': True, 'max_df': 1.0, 'max_features': None, 'min_df': 1, 'ngram_range': (1, 1), 'norm': 'l2', 'preprocessor': None, 'smooth_idf': True, 'stop_words': None, 'strip_accents': None, 'sublinear_tf': False, 'token_pattern': '(?u)\\b\\w\\w+\\b', 'tokenizer': None, 'use_idf': True, 'vocabulary': None}


In [24]:
rotulos_codificados = codificaRotulos(palavras_mais_importantes)

In [25]:
rotulos_codificados

array([2, 0, 0, ..., 0, 1, 1])

In [26]:
NaiveBayes = modeladoraNB(matrizVetores, rotulos_codificados)

              precision    recall  f1-score   support

           0       0.59      0.37      0.46       221
           1       0.88      0.97      0.92      1061
           2       0.81      0.74      0.77       232

    accuracy                           0.85      1514
   macro avg       0.76      0.69      0.72      1514
weighted avg       0.83      0.85      0.83      1514

Acurácia do modelo: 84.68%


In [27]:
SVM = modeladoraSVM(matrizVetores, rotulos_codificados)

              precision    recall  f1-score   support

           0       0.68      0.40      0.50       127
           1       0.86      0.98      0.92       629
           2       0.87      0.69      0.77       153

    accuracy                           0.85       909
   macro avg       0.80      0.69      0.73       909
weighted avg       0.84      0.85      0.83       909

Acurácia do modelo: 84.93%


In [28]:
randomForest = modeladoraRandomForest(matrizVetores, rotulos_codificados)

              precision    recall  f1-score   support

           0       0.75      0.37      0.50       221
           1       0.86      0.98      0.92      1061
           2       0.84      0.70      0.76       232

    accuracy                           0.85      1514
   macro avg       0.81      0.68      0.72      1514
weighted avg       0.84      0.85      0.83      1514

Acurácia do modelo: 84.81%


In [29]:
joblib.dump(NaiveBayes, 'NaiveBayes.pkl')
joblib.dump(SVM, 'SVM.pkl')
joblib.dump(randomForest, 'randomForest.pkl')

['randomForest.pkl']

In [31]:
matrizVetores.shape[1]

6272